In [35]:
import json
from datasets import load_dataset
from tqdm import tqdm

print("start loading dataset")
name = "MCINext/msmarco-fa"
dataset_qrel = load_dataset(name)["train"]

print("start loading corpus")
dataset_corpus_list = load_dataset(name,data_files="corpus.jsonl")["train"]
dataset_corpus = {}
for data in dataset_corpus_list:
    dataset_corpus[str(data["_id"])] = data["text"]

print("start loading queries")
dataset_queries_list = load_dataset(name,data_files="queries.jsonl")["train"]
dataset_queries = {}
for data in dataset_queries_list:
    dataset_queries[str(data["_id"])] = data["text"]


dataset = []
print("start creating dataset")
for data in tqdm(dataset_qrel):

    if data["query-id"] in dataset_queries and data["corpus-id"] in dataset_corpus:
        dataset.append({
            "question": dataset_queries[data["query-id"]],
            "passage_positive": [dataset_corpus[data["corpus-id"]]],
            "passage_negative": [],
            "passage_negative_random": [],
        })

print(f"length of dataset: {len(dataset)}")
with open(f"../../data/v2/msmarco.json", "w") as f:
    json.dump(dataset, f, indent=4, ensure_ascii=False)

start loading dataset
start loading corpus
start loading queries
start creating dataset


100%|██████████| 532751/532751 [00:19<00:00, 27357.60it/s]


length of dataset: 532751


In [75]:
dataset_qrel[10]

{'query-id': '457407', 'corpus-id': '1172', 'score': '1'}

In [77]:
dataset_corpus["1172"]

'سوزوکی SX4 یکی از مطمئن\u200cترین و مقرون به صرفه\u200cترین خودروهای چهارچرخ متحرک است.'

In [81]:
dataset_corpus["1171"]

'فولکس واگن پاسات 4موشن یکی از دست کم گرفته\u200cشده\u200cترین خودروهای بازار کارکرده در شرایط آب و هوایی است. Passat 4Motion با داشتن سیستمی مشابه با چهار چرخ\u200cمحرک\u200cهای افسانه\u200cای آئودی، در سخت\u200cترین شرایط بسیار توانایی دارد.'

In [78]:
dataset_queries["457407"]

'مطمئن ترین خودروهای مقرون به صرفه'

In [68]:
import requests
from dotenv import load_dotenv
import os
import time
from tqdm import tqdm

load_dotenv()

qwen = False
if qwen:
    url = "https://qwen3.chatllm.aiengines.ir/v1/chat/completions"
    model = "Qwen/Qwen3-4B-Instruct-2507"
    headers = {"Content-Type": "application/json", "Authorization": f"Bearer {os.getenv('LLM_AS_RERANKER_PASS')}"}
else:
    url = "http://192.168.130.206:4001/v1/chat/completions"
    model = "google/gemma-3-27b-it"
    headers = {"Content-Type": "application/json"}

instruction = """
You are a helpful assistant that help me remove unclear and vague questions.
I will give you a persian question and you must tell me that we can answer to this question independently or not.

unclear question samples:
- sample 1 : "محتوای این کتاب چیست؟" : {"is_good" : "false"} : because it did not mention the book name
- sample 2 : "چه راه حلی برای این مساله هست؟" : {"is_good" : "false"} : because it did not mention the problem

return {"is_good" : "false"} for unclear questions
otherwise return {"is_good" : "true"}

just return {"is_good" : "true"} or {"is_good" : "false"} in json format nothing else.
"""

for data in dataset[7008:7008+25]:
    print(f"question is : {data['question']}")
    input_message = f"""{{"text": "{data['question']}"}}"""
    messages = [{"role": "system", "content": instruction}, {"role": "user", "content": input_message}]

    payload = {
        "model": model,
        "messages": messages,
        "max_tokens": 100,
    }
    start_time = time.time()
    req = requests.post(url, headers=headers, json=payload)
    print(req.json()['choices'][0]['message']['content'])
    # print(f"time taken: {time.time() - start_time} seconds")
    print("--------------------------------\n")

question is : هلن میرن اینستاگرام
{"is_good": "true"}

--------------------------------

question is : چه گروهی آهنگ پلکان بهشت ​​را خواندند
{"is_good": "true"}

--------------------------------

question is : چه چیزی دیورتیکولیت را تشدید می کند
{"is_good": "true"}

--------------------------------

question is : ژلاتوس چیست
{"is_good" : "true"}

--------------------------------

question is : ایران اسلامی است
{"is_good" : "true"}

--------------------------------

question is : آیا سلول های سرطانی تمایز ضعیفی دارند؟
{"is_good": "true"}

--------------------------------

question is : مالدن مو در کدام شهرستان است
{"is_good" : "true"}

--------------------------------

question is : اعداد رهگیری فدرال اکسپرس چند رقمی هستند
{"is_good" : "true"}

--------------------------------

question is : ایندیاناپولیس آن تا جزیره کینگز چقدر فاصله دارد
{"is_good" : "true"}

--------------------------------

question is : برنامه مسابقات قهرمانان جهان IAAF
{"is_good" : "false"}

-----------------------

In [69]:
dataset[58008:58008+25]

[{'question': 'استفاده از خمیر میسو',
  'passage_positive': ['به جای انبار یا علاوه بر آن استفاده کنید. میسو را می توان در جایی که ممکن است از یک استاک استفاده کنید، یا به جای آن استوک یا برای تقویت طعم یک استاک با طعم کمتر. به جای سس سویا، نمک یا خمیر آنچوی استفاده کنید. این افزودنی\u200cهای نمکی به غذا را می\u200cتوان به راحتی با میسو جایگزین کرد، بدون اینکه جرقه شوری از بین برود.'],
  'passage_negative': [],
  'passage_negative_random': []},
 {'question': 'برای مدیر مدرسه به چه چیزی نیاز دارید',
  'passage_positive': ['در آن مرحله، معلمانی که می خواهند مدیر شوند ممکن است مراحل زیر را دنبال کنند: 1 کسب مدرک کارشناسی ارشد در آموزش، رهبری آموزش و پرورش، یا مدیریت آموزشی.'],
  'passage_negative': [],
  'passage_negative_random': []},
 {'question': 'اساساً جنبه خرده فروشی کسب و کار الکترونیکی است',
  'passage_positive': ['تعریف «خرده فروشی الکترونیکی-خرده فروشی الکترونیکی». فروش کالا و خدمات از طریق اینترنت. خرده\u200cفروشی الکترونیکی یا خرده\u200cفروشی الکترونیکی می\u200cتواند شامل فروش

In [73]:
import requests
from dotenv import load_dotenv
import os
import time
from tqdm import tqdm

load_dotenv()

qwen = False
if qwen:
    url = "https://qwen3.chatllm.aiengines.ir/v1/chat/completions"
    model = "Qwen/Qwen3-4B-Instruct-2507"
    headers = {"Content-Type": "application/json", "Authorization": f"Bearer {os.getenv('LLM_AS_RERANKER_PASS')}"}
else:
    url = "http://192.168.130.206:4001/v1/chat/completions"
    model = "google/gemma-3-27b-it"
    headers = {"Content-Type": "application/json"}

instruction = """
You are a helpful assistant that help to change and modify the question.
I will give you a question and its answer, you must change the question and replace its keywords with synonyms as muuch as possible.
or you can make a new question from the text.

return the question in json format of {"new_question": "new question"}
"""

for data in dataset[7008:7008+25]:
    print(f"question is : {data['question']}")
    print(f"passage is : {data['passage_positive'][0]}")
    input_message = f"""{{"query": "{data['question']}", "passages": {data['passage_positive'][0]}}}"""
    messages = [{"role": "system", "content": instruction}, {"role": "user", "content": input_message}]

    payload = {
        "model": model,
        "messages": messages,
        "max_tokens": 100,
    }
    start_time = time.time()
    req = requests.post(url, headers=headers, json=payload)
    print(req.json()['choices'][0]['message']['content'])
    # print(f"time taken: {time.time() - start_time} seconds")
    print("--------------------------------\n")

question is : هلن میرن اینستاگرام
passage is : صفحه اینستاگرام هلن میرن ساخته شده توسط Fast 8 costar Tyrese. دیم هلن میرن ملکه جدید اینستاگرام است. این بازیگر برنده اسکار به لطف تایرز بازیگر فیلم Fast & Furious 8 که اکانت او را راه اندازی کرد و در همان اولین پست او را مسخره کرد، رسماً در رسانه های اجتماعی حضور دارد. نام کاربری اینستاگرام او ukqueenofhearts@ است و در بیو نوشته شده است، â[Tyrese] این را نوشته است!
```json
{"new_question": "چه کسی صفحه اینستاگرام هلن میرن را ایجاد کرد و نام کاربری او چیست؟"}
```

--------------------------------

question is : چه گروهی آهنگ پلکان بهشت ​​را خواندند
passage is : 1977: گروه راک لد زپلین روی صحنه اجرا کرد. از چپ به راست: جیمی پیج، رابرت پلانت و جان بونهام (1947 - 1980). (عکس از Hulton Archive/Getty Images). âStairway to Heavenâ برای دهه ها جزء اصلی رادیو راک بوده است و هنوز هم در WZLX و در سرتاسر جهان به طور منظم پخش می شود. مسلماً این بزرگترین آهنگ راک تاریخ است. عکس از Hulton Archive/Getty تصاویر). âStairway to Heavenâ برای چندین دهه یکی از

In [3]:
import json

with open("/home/firouzi/embedding_model/data/v2/msmarco.json", "r", encoding="utf-8") as f:
    dataset = json.load(f)


In [50]:
from hazm import word_tokenize, Normalizer, Stemmer


class TextPreprocessor:
    def __init__(self, stopwords_path="/home/firouzi/embedding_model/data_preprocess/stopwords.txt"):
        with open(stopwords_path, encoding='utf-8') as f:
            self.persian_stopwords = set(f.read().splitlines())
        self.normalizer = Normalizer()
        self.stemmer = Stemmer()

    def remove_stopwords(self, text):
        text = self.normalizer.normalize(text)
        tokens = word_tokenize(text)
        stems = [self.stemmer.stem(token) for token in tokens]
        stems = [stem for stem in stems if stem not in self.persian_stopwords]
        return stems
    

    def similar_score(self, query:str, passage:str):
        query_tokens = self.remove_stopwords(query)
        passage_tokens = self.remove_stopwords(passage)

        count = 0
        for token in query_tokens:
            if token in passage_tokens:
                count += 1

        return count / len(query_tokens)


text_preprocessor = TextPreprocessor()


In [52]:
from hazm import Normalizer
import requests
import numpy as np
from dotenv import load_dotenv
import os

load_dotenv()


class TextEmbedder:
    def __init__(self, model_name="BAAI/bge-m3"):
        self.model_name = model_name
        self.headers = {"Content-Type": "application/json", "Authorization": f"Bearer {os.getenv('EMBEDDING_PASS')}"}
        self.normalizer = Normalizer()
    
    def preprocess_embedder(self, text:str):
        text = text.replace("\n", ".")
        text = self.normalizer.normalize(text)
        
        return text
    

    def embed_texts(self, texts:list[str])->list[list[float]]:
        """
        Embed texts using the model.
        """
        if texts == []:
            return []
            
        texts = [self.preprocess_embedder(text) for text in texts]
        
        payload = {
            "model": self.model_name,
            "input": texts
        }
        responses = requests.post("http://78.38.161.78:3094/v1/embeddings", headers=self.headers, json=payload)
        embeddings = [np.array(response["embedding"], dtype=np.float32) for response in responses.json()["data"]]
        
        return embeddings
      
text_embedder = TextEmbedder()

In [ ]:
import requests
from dotenv import load_dotenv
import os
import time
from tqdm import tqdm
import numpy as np


load_dotenv()

qwen = True
if qwen:
    url = "https://qwen3.chatllm.aiengines.ir/v1/chat/completions"
    model = "Qwen/Qwen3-4B-Instruct-2507"
    headers = {"Content-Type": "application/json", "Authorization": f"Bearer {os.getenv('LLM_AS_RERANKER_PASS')}"}
else:
    url = "http://192.168.130.206:4001/v1/chat/completions"
    model = "google/gemma-3-27b-it"
    headers = {"Content-Type": "application/json"}

instruction = """
You are a helpful assistant that help to me to generate a question from the text.
I will give you a text and you must generate a question from the text.

## Rules:
- the question must be in fluent persian
- try to make the question small
- try to use synonyms or similar words instead of exact keywords from the text
- the question must be independent of the text

## Important:
- try to use synonyms or similar words : 
   example : instead of "بهترین خودروی شرکت بنز چیست" you can use "بهترین ماشین شرکت بنز چیست"

- the question must be independent and dont need background information.
   example : instead of "موضوع این کتاب چیست" you can use its book name for example "موضوع کتاب روزگار ابی چیست"

return the question nothing else.
"""

old_similar_score = []
new_similar_score = []

old_embeddings_list = []
new_embeddings_list = []
for data in dataset[8008:8008+25]:
    print(f"question is : {data['question']}")
    print(f"passage is : {data['passage_positive'][0]}")
    input_message = f"""{{"text": {data['passage_positive'][0]}}}"""
    messages = [{"role": "system", "content": instruction}, {"role": "user", "content": input_message}]

    payload = {
        "model": model,
        "messages": messages,
        "max_tokens": 100,
    }
    start_time = time.time()
    req = requests.post(url, headers=headers, json=payload)
    final_text = req.json()['choices'][0]['message']['content']
    print(final_text)
    
    old_score = text_preprocessor.similar_score(data['question'], data['passage_positive'][0])
    new_score = text_preprocessor.similar_score(final_text, data['passage_positive'][0])
    old_similar_score.append(old_score)
    new_similar_score.append(new_score)
    print(f"old similar score: {old_score}")
    print(f"new similar score: {new_score}")

    old_embeddings = text_embedder.embed_texts([data['question'], data['passage_positive'][0]])
    new_embeddings = text_embedder.embed_texts([final_text, data['passage_positive'][0]])
    old_embed_similarity = np.dot(old_embeddings[0], old_embeddings[1])
    new_embed_similarity = np.dot(new_embeddings[0], new_embeddings[1])
    old_embeddings_list.append(old_embed_similarity)
    new_embeddings_list.append(new_embed_similarity)
    print(f"similar old_embeddings: {old_embed_similarity}")
    print(f"similar new_embeddings: {new_embed_similarity}")
    # print(f"time taken: {time.time() - start_time} seconds")
    print("--------------------------------\n")

print(f"old similar score: {np.mean(old_similar_score)}")
print(f"new similar score: {np.mean(new_similar_score)}")
print(f"similar old_embeddings: {np.mean(old_embeddings_list)}")
print(f"similar new_embeddings: {np.mean(new_embeddings_list)}")

question is : آپنکس چیست
passage is : AppNexus AppNexus یک شرکت فناوری جهانی است که پلت فرم نرم‌افزار مبتنی بر ابر آن تبلیغات آنلاین برنامه‌ای را فعال و بهینه می‌کند. رسانه)؛ مایکل روبنشتاین، معاون سابق و مدیر کل دابل کلیک گوگل، در سپتامبر 2009 به عنوان رئیس به AppNexus پیوست.
چه کسی در سپتامبر 2009 به ریاست اپ‌نکسوس منصوب شد؟
old similar score: 0.0
new similar score: 0.4
similar old_embeddings: 0.4430588483810425
similar new_embeddings: 0.5697304010391235
--------------------------------

question is : وضعیت جانبازی ویژه معلول چیست؟
passage is : از آنجایی که جانبازان دارای معلولیت ویژه، کهنه سربازان دوران ویتنام یا سایر کهنه سربازان محافظت شده برای استخدام در نظر گرفته می شوند، فقط آن بخش از اسناد نظامی و معافیت مربوط به شرایط شغلی خاص ممکن است توسط دفتر منابع انسانی بررسی شود.
کدام مدارک نظامی توسط بخش استخدام بررسی می‌گردد؟
old similar score: 0.6666666666666666
new similar score: 0.5714285714285714
similar old_embeddings: 0.5375531911849976
similar new_embeddings: 0.6112977266311646

In [ ]:
import requests
from dotenv import load_dotenv
import os
import time
from tqdm import tqdm
import numpy as np


load_dotenv()

qwen = False
if qwen:
    url = "https://qwen3.chatllm.aiengines.ir/v1/chat/completions"
    model = "Qwen/Qwen3-4B-Instruct-2507"
    headers = {"Content-Type": "application/json", "Authorization": f"Bearer {os.getenv('LLM_AS_RERANKER_PASS')}"}
else:
    url = "http://192.168.130.206:4001/v1/chat/completions"
    model = "google/gemma-3-27b-it"
    headers = {"Content-Type": "application/json"}

instruction = """
You are a helpful assistant that help to me to generate modify and change the input question.
I will give you a question and its text and you must replace the words of question with synonyms or similar words.

## Important:
- replace the words of question with synonyms or similar words.

return the question nothing else.
"""

old_similar_score = []
new_similar_score = []

old_embeddings_list = []
new_embeddings_list = []
for data in dataset[10008:10008+25]:
    print(f"question is : {data['question']}")
    print(f"passage is : {data['passage_positive'][0]}")
    input_message = f"""{{"question": "{data['question']}", "text": {data['passage_positive'][0]}}}"""
    messages = [{"role": "system", "content": instruction}, {"role": "user", "content": input_message}]

    payload = {
        "model": model,
        "messages": messages,
        "max_tokens": 100,
    }
    start_time = time.time()
    req = requests.post(url, headers=headers, json=payload)
    final_text = req.json()['choices'][0]['message']['content']

    print(final_text)
    
    old_score = text_preprocessor.similar_score(data['question'], data['passage_positive'][0])
    new_score = text_preprocessor.similar_score(final_text, data['passage_positive'][0])
    old_similar_score.append(old_score)
    new_similar_score.append(new_score)
    print(f"old similar score: {old_score}")
    print(f"new similar score: {new_score}")

    old_embeddings = text_embedder.embed_texts([data['question'], data['passage_positive'][0]])
    new_embeddings = text_embedder.embed_texts([final_text, data['passage_positive'][0]])
    old_embed_similarity = np.dot(old_embeddings[0], old_embeddings[1])
    new_embed_similarity = np.dot(new_embeddings[0], new_embeddings[1])
    old_embeddings_list.append(old_embed_similarity)
    new_embeddings_list.append(new_embed_similarity)
    print(f"similar old_embeddings: {old_embed_similarity}")
    print(f"similar new_embeddings: {new_embed_similarity}")
    # print(f"time taken: {time.time() - start_time} seconds")
    print("--------------------------------\n")

print(f"old similar score: {np.mean(old_similar_score)}")
print(f"new similar score: {np.mean(new_similar_score)}")
print(f"similar old_embeddings: {np.mean(old_embeddings_list)}")
print(f"similar new_embeddings: {np.mean(new_embeddings_list)}")

question is : اپیتلیال چیست
passage is : اپیتلیوم (epi- + thele + -ium) یکی از چهار نوع اساسی بافت حیوانی است. سه نوع دیگر بافت همبند، بافت عضلانی و بافت عصبی هستند. پوشش مری نمونه‌ای از اپیتلیوم لایه‌ای غیرکراتینیزه یا مرطوب است. انتقالی. اپیتلیوم‌های انتقالی در بافت‌هایی یافت می‌شوند که کشیده می‌شوند و زمانی که بافت کشیده نمی‌شود، می‌تواند به صورت مکعبی طبقه‌بندی شده به نظر برسد یا زمانی که اندام متسع شده و بافت کشیده می‌شود، به‌صورت لایه‌های سنگفرشی به نظر برسد.
اپیتلیال چیست؟
old similar score: 0.0
new similar score: 0.0
similar old_embeddings: 0.522389829158783
similar new_embeddings: 0.5421788096427917
--------------------------------

question is : شماره تلفن کرایه ماشین بدون پرداخت
passage is : 800-729-5377 شماره تلفن خدمات مشتری کرایه اتومبیل Payless است. شماره خدمات مشتری به مشتریان شرکت اجاره خودرو Payless این امکان را می دهد تا شکایات یا پیشنهادات خود را بیان کنند. اگر می خواهید به یک شخص زنده دسترسی پیدا کنید، باید مراحل زیر را دنبال کنید: 1 را فشار دهید. 3 را فشار دهید.
ش